In [ ]:
!pip install transformers
!pip install spacy
!python -m spacy download en_core_web_sm

# NER using Spacy

Spacy's pretrained NER model recognizes the following categories.

    PERSON : Denotes names of people
    GPE : Denotes places like counties, cities, states.
    ORG : Denotes organizations or companies
    WORK_OF_ART : Denotes titles of books, fimls,songs and other arts
    PRODUCT : Denotes products such as vehicles, food items ,furniture and so on.
    EVENT : Denotes historical events like wars, disasters ,etc…
    LANGUAGE : All the recognized languages across the globe.
  

In [ ]:
sample_treccast2019_topic = {
    "number": 1,
    "description": "Considering career options for becoming a physician\u0027s assistant vs a nurse.  Discussion topics include required education (including time, cost), salaries, and which is better overall.",
    "turn": [
      {
        "number": 1,
        "raw_utterance": "What is a physician\u0027s assistant?"
      },
      {
        "number": 2,
        "raw_utterance": "What are the educational requirements required to become one?"
      },
      {
        "number": 3,
        "raw_utterance": "What does it cost?"
      },
      {
        "number": 4,
        "raw_utterance": "What\u0027s the average starting salary in the UK?"
      },
      {
        "number": 5,
        "raw_utterance": "What about in the US?"
      },
      {
        "number": 6,
        "raw_utterance": "What school subjects are needed to become a registered nurse?"
      },
      {
        "number": 7,
        "raw_utterance": "What is the PA average salary vs an RN?"
      },
      {
        "number": 8,
        "raw_utterance": "What the difference between a PA and a nurse practitioner?"
      },
      {
        "number": 9,
        "raw_utterance": "Do NPs or PAs make more?"
      },
      {
        "number": 10,
        "raw_utterance": "Is a PA above a NP?"
      },
      {
        "number": 11,
        "raw_utterance": "What is the fastest way to become a NP?"
      },
      {
        "number": 12,
        "raw_utterance": "How much longer does it take to become a doctor after being an NP?"
      }
    ],
    "title": "Career choice for Nursing and Physician\u0027s Assistant"
  }

In [ ]:
passages = [
    "A physician assistant in the United States, Canada and other select countries or physician associate in the United Kingdom (PA) is an Advanced Practice Provider (APP).",
    "PAs are medical professionals who diagnose illness, develop and manage treatment plans, prescribe medications, and often serve as a patient’s principal healthcare provider.",
    "Jim Kenney, the Democratic mayor of Philadelphia, has just spoken at a press conference with election officials.",
    "The input to BERT is a sequence of words, and the output is a sequence of vectors."
]

In [ ]:
import pprint
import spacy

nlp = spacy.load('en_core_web_sm')

passages_entities = [nlp(p).ents for p in passages]
pprint.pprint(passages_entities)

[(the United States, Canada, the United Kingdom, APP),
 (),
 (Jim Kenney, Democratic, Philadelphia),
 (BERT,)]


In [ ]:
entities_per_passage = []
for passage_entities in passages_entities:
  entities_per_passage.append([[(e.text, e.start_char, e.end_char, e.label_) for e in passage_entities]])
pprint.pprint(entities_per_passage)

[[[('the United States', 25, 42, 'GPE'),
   ('Canada', 44, 50, 'GPE'),
   ('the United Kingdom', 104, 122, 'GPE'),
   ('APP', 162, 165, 'ORG')]],
 [[]],
 [[('Jim Kenney', 0, 10, 'PERSON'),
   ('Democratic', 16, 26, 'NORP'),
   ('Philadelphia', 36, 48, 'GPE')]],
 [[('BERT', 13, 17, 'ORG')]]]


In [ ]:
queries_entities = []
for i in range(len(sample_treccast2019_topic['turn'])):
  utterance = sample_treccast2019_topic['turn'][i]['raw_utterance']
  entities = nlp(utterance).ents
  queries_entities.append([[(e.text, e.start_char, e.end_char, e.label_) for e in entities]])
pprint.pprint(queries_entities)

[[[]],
 [[]],
 [[]],
 [[('UK', 42, 44, 'GPE')]],
 [[('US', 18, 20, 'GPE')]],
 [[]],
 [[('RN', 36, 38, 'ORG')]],
 [[]],
 [[]],
 [[('NP', 16, 18, 'ORG')]],
 [[('NP', 36, 38, 'ORG')]],
 [[('NP', 63, 65, 'ORG')]]]


## Boosting Queries on ElasticSearch

The following function provides a simple implementation to boost entities on query time to interact with the Elastic Search Index.

**You should copy this function to your ElasticSearchSimpleAPI.py file**

In [ ]:
# entities_query_template = {"query": {"bool": {"should": [{"match": {"body": {"query": "Neverending Story", "boost": 1.0}}}, {"match": {"body": "Tell me about the Neverending Story film."}}]}}}

# !pip install elasticsearch
# import ElasticSearchSimpleAPI as es

def search_with_boosted_entities(query_text, entities_list, boost_list, numDocs=10):
  assert len(entities_list) == len(boost_list)
  assert len(entities_list) > 0
  assert isinstance(entities_list[0], str)
  assert isinstance(boost_list[0], (int,float))

  entities_query_template = {"query": {"bool": {"should": [{"match": {"body": query_text}}]}}}
  boost_query_term_template = {"match": {"body": {"query": None, "boost": None}}}

  for i in range(len(entities_list)):
    entity = entities_list[i]
    boost = boost_list[i]
    boost_query_term_template['match']['body']['query'] = entity
    boost_query_term_template['match']['body']['boost'] = boost
    entities_query_template["query"]["bool"]["should"].append(dict(boost_query_term_template))
  
  result = elastic.client.search(index='msmarco', body=entities_query_template, size=numDocs)
  return json_normalize(result["hits"]["hits"])

search_with_boosted_entities('What are the educational requirements required to become one?', ['educational', 'requirements'], [2.0, 1.0])

## Analyzers in Elastic Search

When working with ES, a text processing pipeline is called an Analyzer.
You should carefully consider the text processing pipeline when boosting enitites.
Here is the configuration for our index:

"analysis": {
        "filter": {
          "english_stemmer": {
            "type": "kstem"
          },
          "english_stop": {
            "type": "stop",
            "stopwords_path": "indri.txt"
          },
          "english_possessive_stemmer": {
            "type": "stemmer",
            "language": "possessive_english"
          }
        },
        "analyzer": {
          "rebuilt_english": {
            "filter": [
              "english_possessive_stemmer",
              "lowercase",
              "english_stop",
              "english_stemmer"
            ],
            "tokenizer": "standard"
          }
        }

From: 

{
  "settings": {
    "index": {
      "search": {
        "slowlog": {
          "level": "trace",
          "threshold": {
            "fetch": {
              "warn": "1s",
              "trace": "0ms",
              "debug": "500ms",
              "info": "1ms"
            },
            "query": {
              "warn": "10s",
              "trace": "0ms",
              "debug": "2s",
              "info": "1ms"
            }
          }
        }
      },
      "number_of_shards": "1",
      "provided_name": "msmarco",
      "similarity": {
        "default": {
          "type": "BM25"
        },
        "lmd": {
          "mu": "1000",
          "type": "LMDirichlet"
        }
      },
      "creation_date": "1571155715084",
      "analysis": {
        "filter": {
          "english_stemmer": {
            "type": "kstem"
          },
          "english_stop": {
            "type": "stop",
            "stopwords_path": "indri.txt"
          },
          "english_possessive_stemmer": {
            "type": "stemmer",
            "language": "possessive_english"
          }
        },
        "analyzer": {
          "rebuilt_english": {
            "filter": [
              "english_possessive_stemmer",
              "lowercase",
              "english_stop",
              "english_stemmer"
            ],
            "tokenizer": "standard"
          }
        }
      },
      "number_of_replicas": "0",
      "uuid": "li5OY6rOQeuafF_g9emnuQ",
      "version": {
        "created": "7040099"
      }
    }
  }
}

## More

 - Spacy NER: (https://spacy.io/usage/spacy-101#annotations-ner)

- Elastic Search Boolean Queries:
 - (https://www.elastic.co/blog/how-to-improve-elasticsearch-search-relevance-with-boolean-queries)
 - (https://www.elastic.co/guide/en/elasticsearch/reference/7.4/query-dsl-bool-query.html)

- Elastic Search Query Boosting:
 - (https://www.elastic.co/guide/en/elasticsearch/reference/current/query-dsl-terms-query.html#query-dsl-terms-query)
 - (https://logz.io/blog/elasticsearch-queries/)

